In [2]:
import pandas as pd
from desdeo_emo.EAs import NSGAIII
from desdeo_problem.testproblems import re31, re32, re33, test_problem_builder, vehicle_crashworthiness
from IPython.display import clear_output
from plotly import express as ex

from ipa.domination import non_dominated
from scipy.spatial.distance import cdist

In [4]:
problem = vehicle_crashworthiness()
evolver = NSGAIII(problem, population_size=1000, keep_archive=True)
while evolver.continue_evolution():
    evolver.iterate()

In [9]:
archive = evolver.end()

In [10]:
results = []
for i, item in archive[2].items():
    results.append(item["objectives"])

results = pd.concat(results)

In [11]:
results.reset_index(drop=True, inplace=True)
non_dom = non_dominated(results.to_numpy())
results["non_dominated"] = non_dom

In [12]:
ex.scatter_3d(
    results[results["non_dominated"] == True],
    x=results.columns[0],
    y=results.columns[1],
    z=results.columns[2],
)

In [14]:
results[results["non_dominated"] == True].drop("non_dominated", axis=1).to_csv("../data/VCW.csv", index=False)

In [16]:
problem = re33()
evolver = NSGAIII(problem, population_size=1000, keep_archive=True)
while evolver.continue_evolution():
    evolver.iterate()

archive = evolver.end()
results = []
for i, item in archive[2].items():
    results.append(item["objectives"])

results = pd.concat(results)

results.reset_index(drop=True, inplace=True)
non_dom = non_dominated(results.to_numpy())
results["non_dominated"] = non_dom

ex.scatter_3d(
    results[results["non_dominated"] == True],
    x=results.columns[0],
    y=results.columns[1],
    z=results.columns[2],
)

In [17]:
results[results["non_dominated"] == True].drop("non_dominated", axis=1).to_csv("../data/DBD.csv", index=False)

In [7]:
data = pd.read_csv("../data/DBD.csv")

In [10]:
ex.scatter_3d(data,
    x=data.columns[1],
    y=data.columns[0],
    z=data.columns[2],
              )

In [8]:
distances = cdist(data.to_numpy(), data.to_numpy())
rse = 0
for i in range(distances.shape[0]):
    for j in range(distances.shape[0]):
        if i == j:
            continue
        rse += distances[i, j] ** -2

In [9]:
rse

15400313222803.361

In [220]:
from pymoo.problems import get_problem

In [221]:
# import lhs

from scipy.stats.qmc import LatinHypercube

In [222]:
num_obj = 3
num_dec = 10
num_points = 10000

problem = get_problem("dtlz5", n_var=num_dec, n_obj=num_obj)
dec_vecs = pd.DataFrame(columns=[f"x{i}" for i in range(10)], index=range(num_points))
dec_vecs[[f"x{i}" for i in range(num_obj - 1)]] = LatinHypercube(num_obj - 1).random(num_points)
dec_vecs[[f"x{i}" for i in range(num_obj - 1, 10)]] = 0.5

In [223]:
dec_vecs

x0        x1   x2   x3   x4   x5   x6   x7   x8   x9
0     0.903733  0.062457  0.5  0.5  0.5  0.5  0.5  0.5  0.5  0.5
1     0.544533  0.131826  0.5  0.5  0.5  0.5  0.5  0.5  0.5  0.5
2     0.680102  0.305784  0.5  0.5  0.5  0.5  0.5  0.5  0.5  0.5
3     0.238583  0.430710  0.5  0.5  0.5  0.5  0.5  0.5  0.5  0.5
4     0.007634  0.586880  0.5  0.5  0.5  0.5  0.5  0.5  0.5  0.5
...        ...       ...  ...  ...  ...  ...  ...  ...  ...  ...
9995  0.344603  0.959055  0.5  0.5  0.5  0.5  0.5  0.5  0.5  0.5
9996  0.825747  0.236545  0.5  0.5  0.5  0.5  0.5  0.5  0.5  0.5
9997  0.012164  0.296717  0.5  0.5  0.5  0.5  0.5  0.5  0.5  0.5
9998  0.349916  0.468650  0.5  0.5  0.5  0.5  0.5  0.5  0.5  0.5
9999  0.434796  0.391390  0.5  0.5  0.5  0.5  0.5  0.5  0.5  0.5

[10000 rows x 10 columns]

In [224]:
out_vecs = problem.evaluate(dec_vecs.to_numpy())

In [225]:
ex.scatter_3d(x=out_vecs[:, 0], y=out_vecs[:, 1], z=out_vecs[:, 2])

In [226]:
ex.scatter(x=out_vecs[:, 0], y=out_vecs[:, 1])

In [227]:
np.linalg.norm(out_vecs, axis=1)

array([1., 1., 1., ..., 1., 1., 1.])

In [228]:
out_vecs = pd.DataFrame(out_vecs, columns=[f"f{i}" for i in range(1, num_obj + 1)])
out_vecs.to_csv(f"../data/dtlz5_{num_obj}.csv", index=False)